# Data Visualisation - Lab 6 - Introduction to Interactivity

---

**Authors: Claire Rocks and Richard Kirk**

---

Welcome to the sixth lab for Data Visualisation.

In this lab we are going to look more at introducing interactivity into your visualisations.  Many of the plots we have seen so far have some level of interactivity built in.  In this lab we will be looking at ways in which you can take this a bit further.

We are going to be using a number of libraries.  Many of these we have used many times (such as `pandas` and `plotly`). The main library we will be using is `plotly`, this makes interactive, publication-quality graphs and we saw it when we were looking at geographic data.  We will also be using `ipywidgets` to to generate different types of interactive widgets.

  * `pandas` - data analysis
  * `plotly` - plotting interactive visualisations
  * `ipywidgets` - generates different types of interactive widgets

We are also using the The World Happiness Report 2019, which is a landmark survey of the state of global happiness that ranks 156 countries by how happy their citizens perceive themselves to be. More information on this can be seen [here](https://worldhappiness.report/ed/2019/).

## Setup for the library

In [ ]:
%pip install pandas plotly ipywidgets

import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from ipywidgets import interact
import ipywidgets as widgets

## For VSCode to see the images, we need to alter where images are rendered. This line should sort it out. Comment out these 2 lines if you are running this in Colab
import plotly.io as pio
pio.renderers.default = "notebook"

data = pd.read_csv("happiness-data/2019.csv")
data

## Basic graphs
Plotly Express has some common graphs, including:

  * Bar graphs
  * Histogram graphs
  * Scatter graphs
  * Line graphs
  * Box 
  
Lets start by drawing a bar chart of 'Overall rank' vs 'GDP per capita' and add some interactivity to it.

In [ ]:
figBar = px.bar(data, x='Overall rank', y='GDP per capita', title='Happiness Rank over GDP per capita')
go.FigureWidget(figBar)

Plotly has a lot of interactivity built in. We can hover over the bars and see the values and in the top right we see buttons to zoom, pan and download as a `.png` image.

Lets have a look at some of the other ways we can build in extra information.

### Adding colour

We can represent another dimension in the data using colour. We can either pass a static value, an array, or a column from the dataset which can be used to colourise the graph. In this case, we have decided to the the last option by setting the parameter `color` to `'Generosity'`.

In [ ]:
figBar = px.bar(data, x='Overall rank', y='GDP per capita', color='Generosity', title='Does having and giving your money away make you happier?')
go.FigureWidget(figBar)

### Additional Data

We can specify additional details to be included in the hover text by adding the column name to an array, and pass it to the parameter `hover_data`.

In [ ]:
figBar = px.bar(data, x='Overall rank', y='GDP per capita', color='Generosity', hover_data=['Country or region'], title='Does having and giving your money away make you happier?')
go.FigureWidget(figBar)

We can print values on to the graph and limit the range of values that we show, through the use of `text_auto`. To make it easier to see, we are also going to limit the range of the x-axis to just the first 50 bars (done through the use of the parameter `range_x`).

In [ ]:
figBar = px.bar(data, x='Overall rank', y='GDP per capita', color='Generosity', hover_data=['Country or region'], text_auto='.2s', 
                title='Does having and giving your money away make you happier?', range_x=(0.5,50.5))
go.FigureWidget(figBar)
figBar.show()

We can also alter how the text is presented by updating the traces once we have all the data. We'll look at more examples of [data](https://plotly.com/python/creating-and-updating-figures/), [layout](https://plotly.com/python/reference/layout/) and [trace](https://plotly.com/python-api-reference/generated/plotly.graph_objects.Figure.html#plotly.graph_objects.Figure.update_traces) updates during this lab and further labs.

In [ ]:
figBar = px.bar(data, x='Overall rank', y='GDP per capita', color='Generosity', hover_data=['Country or region'], text_auto='.2s',
                title='Does having and giving your money away make you happier?', range_x=(0.5,50.5))
figBar.update_traces(textfont_size=30, textangle=0, textposition="outside", cliponaxis=False)
go.FigureWidget(figBar)

## Auto-Updating graphs

Up to now, we have been drawing a new figure each time we make an update. Lets look at how we can generate a single figure and update it.

In [ ]:
blank = go.FigureWidget()
blank

### Adding data

We can now add scatter and bar charts to the blank figure. If you look back at the previous code block once you run one or both of the following, you'll see that the figure will have updated

In [ ]:
## Adds a scatter plot based on the GDP
blank.add_scatter(y=data['GDP per capita'], name='GDP per capita');

In [ ]:
## Adds a bar plot based on the Score
blank.add_bar(y=data['Score']);

### Modifying the graph

Our updates don't have to be limited to just adding new graphs. We can modify the data we already have...

In [ ]:
bars = blank.data[1]
bars.y = data['Social support']
bars.name = 'Social support'

... and the layout of the graph!

In [ ]:
blank.layout.xaxis.title = 'Rank'
blank.layout.yaxis.title = 'Relative Value'
blank.layout.title.text = 'Measure of Happiness'

There are lots of ways in which you can refine the appearance of the graph and the way in which you present the data - maybe you have found more as you attempted the earlier exercises. In the remainder of this lab we want to show you how you can use **ipywidgets** to add additional interactivity.

## Adding further interactivity to the visualisation

For this section, to make life easier, we will be creating a duplicate graph called `figBarWidget`... Note that for this, we are required to use `FigureWidget` rather than `Figure` so that it updates in real time.

In [ ]:
figBarWidget = go.FigureWidget(figBar)
figBarWidget

### Adding a selector

Wouldn't it be cool if we could change which column we map onto the y-axis? We can do this! To do this, we can create a selector widget, and attach it to a function (by putting the `@interact` statement just before the function definition). We also need to inform the figure that there has been a bunch of updates, by using the line `with figBarWidget.batch_update():`.

In [ ]:
bars = figBarWidget.data[0]
@interact(Source = ['GDP per capita', 'Social support'])
def update1(Source = 'GDP per capita'):
    with figBarWidget.batch_update():
        bars.y = data[Source]
        bars.name = Source
        figBarWidget.layout.yaxis.title = Source

### Adding a slider

It's not just text selectors we are limited to, we can create sliders! Lets utilise one to set the number of elements we represent. Remember, when we change something on the widget, it updates the `figBarWidget` figure from a couple of code blocks ago!

In [ ]:
@interact(NumRanks = (1,156,1))
def update2(NumRanks = 100):
    with figBarWidget.batch_update():
        figBarWidget.layout.xaxis.range=(0.5,NumRanks+0.5)

### Adding custom widgets

We aren't limited to 2, there are loads of different widgets we can pick! The ones shown so far are the most common and as such, have a short hand syntax. We can see a list of widgets [here](https://ipywidgets.readthedocs.io/en/latest/examples/Widget%20List.html), and utilise these when stating the widgets.

In [ ]:
@interact(x = widgets.IntRangeSlider(value=[20,50], min=0, max=165, description="Rank Range: "))
def update3(x = (20,50)):
    with figBarWidget.batch_update():
        figBarWidget.layout.xaxis.range=(x[0]+0.5,x[1]+0.5)

It should also be noted that we aren't limited to a single widget per function. We can have as many as we want! Further information how the `@interact` statement works and further utilised can be found [here](https://ipywidgets.readthedocs.io/en/latest/examples/Using%20Interact.html).

### Combining widgets
What if want to include the interactivity as part of the plot? First off, lets create 3 widgets and use these to define how they would interact with the graph. Some of these will be very familiar...!

In [ ]:
## Create some static widgets we can refer back to!
source_widget = widgets.Dropdown(options = ['GDP per capita', 'Social support'], description="Source: ")
yAxis_widget = widgets.FloatSlider(value = 1.5, min = 0.0, max = 3.0, description = "Y axis max: ", readout_format='.1f', readout=True)
rankRange_widget = widgets.IntRangeSlider(value=[20,50], min=0, max=165, description="Rank Range: ")

bars = figBarWidget.data[0]
@interact(Source = source_widget)
def update1(Source = 'GDP per capita'):
    with figBarWidget.batch_update():
        bars.y = data[Source]
        bars.name = Source
        figBarWidget.layout.yaxis.title = Source

@interact(x = yAxis_widget)
def update2(x = 1.5):
    with figBarWidget.batch_update():
        figBarWidget.layout.yaxis.range = (0, x)

@interact(x = rankRange_widget)
def update3(x = (20,50)):
    with figBarWidget.batch_update():
        figBarWidget.layout.xaxis.range = (x[0]+0.5,x[1]+0.5)

Once we have all the widgets have been defined, we can organise them in different ways. One of the easiest way to do this is to use vertical and horizontal boxes (referred to as `VBox` and `HBox` respectively). Each of these takes an array of widgets, with optional extra parameters.

In [ ]:
## Lets have a vertical box containing all our controls
control_widgets = widgets.VBox([source_widget, yAxis_widget, rankRange_widget],layout=widgets.Layout(justify_content='space-around'))

overall_fig = widgets.HBox([control_widgets, figBarWidget])
overall_fig

If you want to find more layouts, have a look at the list of widgets page found [here](https://ipywidgets.readthedocs.io/en/latest/examples/Widget%20List.html#Container/Layout-widgets).

## Animations

Who doesn't like moving pictures! In this section, we will be looking at how we can use **ipywidgets** to auto-update a figure.

### Adding control buttons

First off, lets create a widget for the set of controls. Whilst we could manually create these using `widgets.Button` and a `widgets.HBox`, it is so much easier to use the `widgets.Play` widget which does all this for us...

In [ ]:
play = widgets.Play(min=0, max=156, step=1, interval=500, value=50)
play

### Adding timer bar

One thing you will notice is that the `widgets.Play` has no indication on where we are through the available time. As such, lets create a slider that we can use as an indicator.

In [ ]:
slider = widgets.IntSlider(min=0, max=156, description="", disabled=True)
slider

### Linking widgets

Now that we have the two widgets, we need to make sure they read of the same `value` element. To do this, we need to `link` them together...

In [ ]:
widgets.link((play, 'value'), (slider, 'value'))

### Displaying multiple widgets

Finally, lets put them together into a nice, single widget!

In [ ]:
playControls = widgets.HBox([play, slider])
playControls

### Setting up interaction

In order to link this to the figure, we can use `@interact` as we discussed previously. However, `@interact` will only accept widgets that are used for the function. Therefore, we need to pull out the correct widget for the function using the `children` function. Alternatively, we could use the `play` widget we defined earlier!

In [ ]:
@interact(x=playControls.children[0])
def update4(x):
    with figBarWidget.batch_update():
        figBarWidget.layout.xaxis.range=(0.5,x+0.5)

## Exercise 1 - Adding further interactivity
Build a collection of widgets that can do the following to the figure `exerciseFigBar` provided bellow:
  * Alters the colour to a given attribute
  * Scales the y axis range
  * Adds/Removes a line graph of the *Healthy life expectancy* depending on if a button is pressed or not (have a look at `widgets.ToggleButton`)
  * Highlights a given country to bright green (have a look at [this](https://plotly.com/python/bar-charts/#customizing-individual-bar-colors) for more info on altering individual columns) (widget ideas include `widgets.RadioButtons`, `widgets.Select` and `widgets.Combobox`)

In [ ]:
exerciseFig = px.bar(data, x='Overall rank', y='GDP per capita', title='Happiness Rank over GDP per capita')
exerciseFigBar = go.FigureWidget(exerciseFig)
exerciseFigBar

In [ ]:
## Exercise 1 code here! ##

## Exercise 2 
### Part A - Custom graphs
Create a new figure widget that shows each of the attributes in the happiness dataset (except happiness rank, happiness score and country) against their happiness score (where happiness score is on the x axis). You should provide functionality that will allow for 1 or more attributes to be displayed at the same time.

In [ ]:
## Exercise 2A code here! ##

### Part B - Expanding the functionality
Extend the graph made in Exercise 2 Part A to allow for any attribute to be used on the x axis. This attribute should not appear in the list of possible attributes that can be displayed against it. For example, if 'GDP per capita' is picked for the x axis, then you should be able to display any number of the other attributes (including happiness score).

In [ ]:
## Exercise 2B code here! ##

## Bonus Exercise
In the Bonus Exercise for Lab 2, we scraped data from the BBC Weather API feed. This provided data at the current time, for a given location ID. It turns out that that this is not the only feed the BBC Weather API has... it also has a 3 day forecast feed. This can be found [here](https://weather-broker-cdn.api.bbci.co.uk/en/forecast/rss/3day/2652221), and works in a similar way to the previous feed. It requires a 7 digit ID which will correspond to a given area, and will produce an XML document that will contain 3 items, each relating to a particular day.

Using the skills gained from Labs 2, 5 and 6 (this lab...), produce a timeline visualisation of the weather in Coventry (ID: 265221) for the next 3 days.

In [ ]:
## Bonus Exercise code here! ##